In [136]:
import gensim
import gensim.corpora as corpora
import logging
import nltk
import matplotlib.pyplot as plt
import os
import pandas as pd
import pickle
import pyLDAvis
import pyLDAvis.gensim  # don't skip this
import warnings

from collections import defaultdict
from datetime import datetime
from gensim.models import CoherenceModel, Phrases, HdpModel, LsiModel
from gensim.utils import simple_preprocess
from gensim.models.phrases import Phraser
from glob import glob
from nltk.corpus import stopwords
from nltk.stem.wordnet import WordNetLemmatizer
from pprint import pprint
from sqlalchemy import create_engine
from tqdm import tqdm_notebook

#from transform import apply_filters, transform_body

%matplotlib inline

logging.basicConfig(level=logging.ERROR)
warnings.filterwarnings("ignore", category=DeprecationWarning)

tqdm_notebook().pandas()
pyLDAvis.enable_notebook()

nltk.download('stopwords')

STOP_WORDS = stopwords.words('english')
STOP_WORDS.extend(['gt', 'ymy', 'hi', 'get', 'thi', 'http', 
                   'ha', 'amp', 'nbsp', 'amp_nbsp', 'http', 'https', 'www', 
                   'com', 'message_moderators', 'like', 'also', 'regardless'])
STOP_WORDS.extend(load_filters("body"))
STOP_WORDS = set(STOP_WORDS)

[nltk_data] Downloading package stopwords to
[nltk_data]     /home/jessica/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
Blacklists: data/filtering/body/custom_stopwords.txt


In [137]:
def run(tag, subreddit, num_topics_list=range(3, 13), ngrams=3):
    root_path = "output/"+tag
    os.mkdir(root_path)
    
    # Load data
    observations = load_data_from_psql(["AskWomen"], table_name="preprocessed_posts")
    print(str(observations.head()))
    logging.debug(observations.head())
        
    # Transform data
    tokenized_data = transform(observations, ngrams=ngrams, threshold=50)
    id2word = corpora.Dictionary(tokenized_data)

    texts = tokenized_data
    corpus = [id2word.doc2bow(text) for text in texts]
    
    # archive texts
    with open(root_path+"/tokenized_docs.txt", "w") as outfile:
        outfile.write('\n'.join(str(texts)))
                    
    # Word frequency
    word_freq = get_word_freq(id2word, corpus)
    with open(root_path+"/word_frequency.txt", "w") as outfile:
        outfile.write('\n'.join([str(w) for w in word_freq]))
    
    for num_topics in num_topics_list:
        # Make dir
        path = root_path+"/"+str(num_topics)
        os.mkdir(path)
        
        # Model
        lda_model = get_model(corpus, id2word, num_topics, use_tfidf=True, use_lsi=False)

        with open(path+"/model.pkl", "wb") as pfile:
            pickle.dump(lda_model, pfile)
            
        # Topic weights
        pprint(lda_model.print_topics())
        with open(path+"/topics.txt", "w") as outfile:
            outfile.write('\n'.join([str(i) for i in lda_model.show_topics()]))
        
        # Metrics (coherence model)
        coherence_model_lda = CoherenceModel(model=lda_model, texts=texts,
            dictionary=id2word, coherence='c_v')
        with open(path+"/coherence_model.pkl", "wb") as pfile:
            pickle.dump(coherence_model_lda, pfile)
            
        #coherence_score = str(coherence_model_lda.get_coherence())
        #logging.info('\nCoherence Score: ' + coherence_score)
        #with open(path+"/coherence_score.txt", "w") as outfile:
        #    outfile.write(coherence_score)
        
        # Viz
        vis = pyLDAvis.gensim.prepare(lda_model, corpus, id2word)
        with open(path+"/results.html", "w") as outfile:
            pyLDAvis.save_html(data=vis, fileobj=outfile)
            

######### Model
def get_model(corpus, id2word, num_topics, use_tfidf=False, use_lsi=False, use_hdp=False):

    if use_tfidf:
        tfidf_model = gensim.models.TfidfModel(corpus, id2word=id2word)
        corpus = tfidf_model[corpus]
        
    if use_hdp:
        hdp_model = HdpModel(corpus=corpus, id2word=id2word, chunksize=500,
                            max_chunks=num_topics)
        return hdp_model
    
    if use_lsi:
        lsi_model = LsiModel(corpus=corpus, id2word=id2word, chunksize=1000,
                            num_topics=num_topics)
        return lsi_model

    lda_model = gensim.models.ldamodel.LdaModel(
        corpus=corpus, id2word=id2word, num_topics=num_topics,
        update_every=1, chunksize=1000, passes=5, alpha='auto',
        per_word_topics=True, iterations=35
    )
    return lda_model
        
            
######### Extract
def load_data_from_psql(subreddits, table_name, maxlen=None, log_level=logging.INFO):
    QUERY = "SELECT author, body, subreddit from " + table_name + " where subreddit in {}"
    PSQL = 'postgres://{}@localhost:5432/reddit_topics'
    
    cred = ""
    with open("credentials/localhost/jessica.txt") as credfile:
        cred = credfile.read().strip("\n")

    cnx = create_engine(PSQL.format(cred), isolation_level='AUTOCOMMIT')
    read_query = QUERY.format("('"+"','".join(subreddits)+"') {}")
    if maxlen:
        read_query = read_query.format("LIMIT " + maxlen + ";")
    else:
        read_query = read_query.format(";")
    return pd.read_sql_query(read_query, cnx)


######### Transform
def transform(observations, ngrams=2, threshold=100):
    author_blacklist = load_filters("author")
    print("Removing bots and suspicious authors")
    #observations = apply_filters.filter(observations)
    observations = observations[~observations['author'].isin(author_blacklist)]
       
    print("Preprocessing")
    preprocess_body = observations['body'].progress_apply(preprocess)
    data_words = list(preprocess_body.values)
    
    data_words_nostops = remove_stopwords(data_words)
    
    if ngrams > 1:
        bigram = Phrases(data_words_nostops, min_count=5, threshold=threshold) # higher threshold fewer phrases.
        trigram = Phrases(bigram[data_words_nostops], threshold=threshold)  

        # Faster way to get a sentence clubbed as a trigram/bigram
        bigram_mod = Phraser(bigram)
        trigram_mod = Phraser(trigram)
    
        def make_bigrams(texts):
            return [bigram_mod[doc] for doc in texts]

        def make_trigrams(texts):
            return [trigram_mod[bigram_mod[doc]] for doc in texts]

        if ngrams == 3:
            return make_trigrams(data_words_nostops)
        elif ngrams == 2:
            return make_bigrams(data_words_nostops)
    else:
        return data_words_nostops

def preprocess(text):
    wnl = WordNetLemmatizer()
    text = text.replace("'", "")
    text = text.replace('"', "")
    words = gensim.utils.simple_preprocess(text, deacc=True)
    words = [wnl.lemmatize(word, pos='v') for word in words]
    words = [word for word in words if word not in STOP_WORDS]
    return words
    
def remove_stopwords(texts):
    return [[word for word in simple_preprocess(str(doc)) if word not in STOP_WORDS] for doc in texts]

def load_filters(t):
    filter_path = "data/filtering/{}/*.txt"
    blacklist = []
    paths = glob(filter_path.format(t))
    print("Blacklists: " + " ".join(paths))
    for path in paths:
        with open(path, "r") as ffile:
             lines = ffile.readlines()
        blacklist.extend([l.replace("\n", "") for l in lines])
    return blacklist    

# Debug
def get_word_freq(id2word, corpus, limit=None):
    count = defaultdict(int)
    for cp in corpus:
        for tup in cp:
            count[id2word[tup[0]]] += tup[1]
    if limit==None:
        limit=len(count)
    return sorted(count.items(), reverse=True, key=lambda x: x[1])[:limit]


In [138]:
ngrams=2
topics = [11, 13, 26, 27, 28, 29, 31]
now = datetime.now().strftime("%Y_%m_%d_%H%M")
tag = "AskWomen_ldafinal_moretopics_"+now

params = {}
params["num_topics"] = topics
params["ngrams_threshold"] = 50
params["model"] = "LDA"
params["iterations"] = 25
params["min_df"] = 5

run(tag, "AskWomen", num_topics_list=topics, ngrams=ngrams)

with open("output/"+tag+"/params.txt", "w") as outfile:
    for k, v in params.items():
        outfile.write('%s: %s' % (k, str(v)))
        

           author       body subreddit
0       [deleted]  [deleted]  AskWomen
1       [deleted]  [deleted]  AskWomen
2       [deleted]  [deleted]  AskWomen
3       [deleted]  [deleted]  AskWomen
4  ffreudiannipss      No/no  AskWomen
Blacklists: data/filtering/author/reddit_bots.txt data/filtering/author/suspicious_authors.txt
Removing bots and suspicious authors
Preprocessing


INFO:gensim.models.phrases:collecting all words and their counts
INFO:gensim.models.phrases:PROGRESS: at sentence #0, processed 0 words and 0 word types
INFO:gensim.models.phrases:PROGRESS: at sentence #10000, processed 202077 words and 154846 word types
INFO:gensim.models.phrases:PROGRESS: at sentence #20000, processed 409477 words and 278687 word types
INFO:gensim.models.phrases:PROGRESS: at sentence #30000, processed 612497 words and 391448 word types
INFO:gensim.models.phrases:PROGRESS: at sentence #40000, processed 808830 words and 493732 word types
INFO:gensim.models.phrases:PROGRESS: at sentence #50000, processed 1005207 words and 589845 word types
INFO:gensim.models.phrases:PROGRESS: at sentence #60000, processed 1206103 words and 681011 word types
INFO:gensim.models.phrases:PROGRESS: at sentence #70000, processed 1414355 words and 773798 word types
INFO:gensim.models.phrases:PROGRESS: at sentence #80000, processed 1622576 words and 861280 word types
INFO:gensim.models.phrases:

INFO:gensim.models.ldamodel:merging changes from 1000 documents into a model of 104071 documents
INFO:gensim.models.ldamodel:topic #6 (0.086): 0.006*"hairstyle" + 0.005*"barron" + 0.005*"tbh" + 0.005*"personally" + 0.004*"change" + 0.004*"adorable" + 0.004*"guy" + 0.004*"liquorice" + 0.004*"care" + 0.004*"things"
INFO:gensim.models.ldamodel:topic #5 (0.086): 0.050*"askwomen" + 0.024*"reddit" + 0.009*"act_upon" + 0.009*"give_mod" + 0.009*"understand_reason" + 0.008*"reddit_wiki" + 0.008*"action_click" + 0.008*"question_moderator" + 0.007*"reddit_compose" + 0.005*"texture"
INFO:gensim.models.ldamodel:topic #10 (0.092): 0.006*"nice" + 0.006*"people" + 0.005*"write" + 0.005*"women" + 0.004*"good" + 0.004*"olives" + 0.004*"taste" + 0.004*"give" + 0.004*"make" + 0.004*"try"
INFO:gensim.models.ldamodel:topic #3 (0.093): 0.009*"big_deal" + 0.005*"people" + 0.005*"way" + 0.004*"hate" + 0.004*"guy" + 0.004*"course" + 0.004*"women" + 0.004*"one" + 0.004*"reply" + 0.004*"care"
INFO:gensim.models.l

INFO:gensim.models.ldamodel:topic #0 (0.144): 0.008*"im" + 0.007*"want" + 0.007*"feel" + 0.006*"make" + 0.006*"see" + 0.004*"happen" + 0.004*"time" + 0.004*"something" + 0.004*"one" + 0.004*"youre"
INFO:gensim.models.ldamodel:topic diff=0.202898, rho=0.377964
INFO:gensim.models.ldamodel:PROGRESS: pass 0, at document #8000/104071
INFO:gensim.models.ldamodel:optimized alpha [0.15693831, 0.103246704, 0.11133095, 0.13139766, 0.10264224, 0.09213952, 0.107233316, 0.1561353, 0.0982969, 0.10746398, 0.13320038]
INFO:gensim.models.ldamodel:merging changes from 1000 documents into a model of 104071 documents
INFO:gensim.models.ldamodel:topic #5 (0.092): 0.107*"askwomen" + 0.054*"reddit" + 0.018*"reddit_wiki" + 0.018*"act_upon" + 0.018*"give_mod" + 0.018*"understand_reason" + 0.016*"action_click" + 0.016*"question_moderator" + 0.016*"reddit_compose" + 0.008*"question"
INFO:gensim.models.ldamodel:topic #8 (0.098): 0.016*"thank" + 0.010*"derail" + 0.009*"bisexual" + 0.007*"wax" + 0.005*"exist" + 0.0

INFO:gensim.models.ldamodel:topic #8 (0.107): 0.031*"thank" + 0.010*"wax" + 0.010*"taller" + 0.006*"eyebrows" + 0.006*"creepy" + 0.005*"derail" + 0.005*"bigger" + 0.005*"style" + 0.004*"bisexual" + 0.004*"heat"
INFO:gensim.models.ldamodel:topic #3 (0.175): 0.008*"dog" + 0.006*"cat" + 0.006*"eat" + 0.005*"clothe" + 0.005*"hate" + 0.005*"use" + 0.005*"height" + 0.005*"im" + 0.005*"wear" + 0.004*"never"
INFO:gensim.models.ldamodel:topic #0 (0.222): 0.011*"im" + 0.008*"feel" + 0.006*"make" + 0.005*"want" + 0.005*"hes" + 0.005*"youre" + 0.005*"ask" + 0.005*"happen" + 0.005*"time" + 0.005*"way"
INFO:gensim.models.ldamodel:topic #7 (0.256): 0.009*"time" + 0.007*"im" + 0.006*"want" + 0.006*"relationship" + 0.006*"always" + 0.006*"love" + 0.005*"one" + 0.005*"touch" + 0.004*"alone" + 0.004*"sex"
INFO:gensim.models.ldamodel:topic diff=0.173024, rho=0.277350
INFO:gensim.models.ldamodel:PROGRESS: pass 0, at document #14000/104071
INFO:gensim.models.ldamodel:optimized alpha [0.24045229, 0.112598635

...

INFO:gensim.models.ldamodel:merging changes from 1000 documents into a model of 104071 documents
INFO:gensim.models.ldamodel:topic #0 (0.343): 0.016*"boss" + 0.014*"discuss" + 0.012*"toy" + 0.011*"video" + 0.011*"ahead" + 0.010*"rock" + 0.010*"racism" + 0.010*"assets" + 0.010*"project" + 0.010*"neck"
INFO:gensim.models.ldamodel:topic #5 (0.363): 0.018*"wonderful" + 0.015*"ouija_board" + 0.015*"lovely" + 0.014*"kick" + 0.013*"fairly" + 0.011*"orgasm" + 0.009*"undercut" + 0.009*"fart" + 0.008*"october" + 0.008*"ride"
INFO:gensim.models.ldamodel:topic #16 (4.491): 0.018*"right" + 0.018*"wear" + 0.013*"sound" + 0.012*"book" + 0.011*"name" + 0.011*"big" + 0.011*"hair" + 0.010*"experience" + 0.010*"days" + 0.009*"sleep"
INFO:gensim.models.ldamodel:topic #2 (5.530): 0.015*"person" + 0.015*"read" + 0.014*"back" + 0.013*"keep" + 0.012*"watch" + 0.012*"hes" + 0.011*"put" + 0.011*"question" + 0.010*"best" + 0.010*"ill"
INFO:gensim.models.ldamodel:topic #12 (17.652): 0.014*"im" + 0.010*"make" + 0.

INFO:gensim.models.ldamodel:merging changes from 1000 documents into a model of 104071 documents
INFO:gensim.models.ldamodel:topic #0 (0.347): 0.019*"rock" + 0.017*"boss" + 0.016*"toy" + 0.014*"video" + 0.013*"project" + 0.012*"discuss" + 0.011*"upon" + 0.009*"ahead" + 0.009*"assets" + 0.008*"neck"
INFO:gensim.models.ldamodel:topic #5 (0.370): 0.016*"wonderful" + 0.013*"kick" + 0.013*"fairly" + 0.013*"lovely" + 0.013*"weather" + 0.012*"reasonable" + 0.012*"jewelry" + 0.010*"ouija_board" + 0.009*"orgasm" + 0.008*"october"
INFO:gensim.models.ldamodel:topic #16 (4.539): 0.019*"wear" + 0.018*"right" + 0.013*"sound" + 0.011*"book" + 0.010*"experience" + 0.010*"days" + 0.010*"big" + 0.010*"hope" + 0.009*"hair" + 0.009*"name"
INFO:gensim.models.ldamodel:topic #2 (5.595): 0.015*"person" + 0.013*"back" + 0.013*"read" + 0.012*"watch" + 0.012*"keep" + 0.011*"question" + 0.011*"hes" + 0.011*"ill" + 0.011*"last" + 0.011*"put"
INFO:gensim.models.ldamodel:topic #12 (17.870): 0.014*"im" + 0.010*"make"

INFO:gensim.models.ldamodel:merging changes from 1000 documents into a model of 104071 documents
INFO:gensim.models.ldamodel:topic #0 (0.352): 0.022*"boss" + 0.020*"toy" + 0.019*"rock" + 0.014*"discuss" + 0.013*"project" + 0.012*"ahead" + 0.011*"upon" + 0.011*"initiate" + 0.009*"video" + 0.009*"neck"
INFO:gensim.models.ldamodel:topic #5 (0.376): 0.016*"kick" + 0.015*"fairly" + 0.015*"wonderful" + 0.014*"jewelry" + 0.012*"weather" + 0.012*"lovely" + 0.009*"reasonable" + 0.008*"fart" + 0.008*"request" + 0.008*"orgasm"
INFO:gensim.models.ldamodel:topic #16 (4.594): 0.018*"wear" + 0.017*"right" + 0.013*"experience" + 0.012*"sound" + 0.011*"hair" + 0.011*"sleep" + 0.010*"days" + 0.010*"book" + 0.009*"big" + 0.009*"hope"
INFO:gensim.models.ldamodel:topic #2 (5.671): 0.015*"person" + 0.014*"back" + 0.012*"keep" + 0.012*"question" + 0.012*"home" + 0.012*"hes" + 0.011*"read" + 0.011*"put" + 0.011*"sometimes" + 0.011*"ill"
INFO:gensim.models.ldamodel:topic #12 (18.136): 0.014*"im" + 0.010*"peopl

INFO:gensim.models.ldamodel:merging changes from 71 documents into a model of 104071 documents
INFO:gensim.models.ldamodel:topic #0 (0.359): 0.025*"boss" + 0.021*"trail" + 0.021*"ditto" + 0.019*"ahead" + 0.017*"woah" + 0.017*"toy" + 0.014*"squash" + 0.014*"rock" + 0.013*"discuss" + 0.013*"glance"
INFO:gensim.models.ldamodel:topic #5 (0.381): 0.025*"kick" + 0.020*"fairly" + 0.014*"wonderful" + 0.013*"jewelry" + 0.011*"reasonable" + 0.010*"closest" + 0.009*"lovely" + 0.009*"hysterectomy" + 0.009*"weather" + 0.009*"fart"
INFO:gensim.models.ldamodel:topic #16 (4.661): 0.016*"right" + 0.015*"wear" + 0.014*"sound" + 0.014*"experience" + 0.013*"sleep" + 0.012*"days" + 0.011*"old" + 0.011*"wish" + 0.010*"hope" + 0.009*"vacation"
INFO:gensim.models.ldamodel:topic #2 (5.748): 0.016*"person" + 0.015*"back" + 0.014*"hes" + 0.013*"home" + 0.013*"keep" + 0.012*"stop" + 0.012*"question" + 0.011*"ill" + 0.010*"put" + 0.010*"sometimes"
INFO:gensim.models.ldamodel:topic #12 (18.436): 0.014*"im" + 0.011*

[(0,
  '0.025*"boss" + 0.021*"trail" + 0.021*"ditto" + 0.019*"ahead" + 0.017*"woah" '
  '+ 0.017*"toy" + 0.014*"squash" + 0.014*"rock" + 0.013*"discuss" + '
  '0.013*"glance"'),
 (5,
  '0.025*"kick" + 0.020*"fairly" + 0.014*"wonderful" + 0.013*"jewelry" + '
  '0.011*"reasonable" + 0.010*"closest" + 0.009*"lovely" + '
  '0.009*"hysterectomy" + 0.009*"weather" + 0.009*"fart"'),
 (28,
  '0.027*"report" + 0.025*"quality" + 0.023*"relax" + 0.020*"moms" + '
  '0.017*"crisis" + 0.017*"jail" + 0.014*"um" + 0.013*"service" + '
  '0.012*"treatment" + 0.011*"chill"'),
 (3,
  '0.184*"askwomen" + 0.085*"reddit" + 0.032*"act_upon" + '
  '0.032*"understand_reason" + 0.032*"give_mod" + 0.031*"reddit_wiki" + '
  '0.029*"question_moderator" + 0.029*"action_click" + 0.028*"reddit_compose" '
  '+ 0.015*"ye"'),
 (11,
  '0.017*"professional" + 0.016*"industry" + 0.016*"reference" + '
  '0.013*"polite" + 0.013*"strange" + 0.012*"maintain" + 0.012*"genuinely" + '
  '0.011*"length" + 0.010*"escalate" + 0.009*"

In [139]:
root_path = "output/"+tag+"/"
for i in topics:
    path = root_path+str(i)
    coherence_model = None
    with open(path + "/coherence_model.pkl", "rb") as cfile:
        coherence_model = pickle.load(cfile)
        coherence_score = str(coherence_model.get_coherence())
        print(str(i) + " Topics: " + coherence_score)
        with open(path+"/coherence_score.txt", "w") as outfile:
            outfile.write(coherence_score)
            
# [0.70, 0.67, 0.65, 0.64, 0.58, 0.52, 0.55, 0.51, 0.48, 0.49]

INFO:gensim.topic_coherence.probability_estimation:using ParallelWordOccurrenceAccumulator(processes=3, batch_size=64) to estimate probabilities from sliding windows
INFO:gensim.topic_coherence.text_analysis:serializing accumulator to return to master...
INFO:gensim.topic_coherence.text_analysis:serializing accumulator to return to master...
INFO:gensim.topic_coherence.text_analysis:serializing accumulator to return to master...
INFO:gensim.topic_coherence.text_analysis:accumulator serialized
INFO:gensim.topic_coherence.text_analysis:accumulator serialized
INFO:gensim.topic_coherence.text_analysis:accumulator serialized
INFO:gensim.topic_coherence.text_analysis:3 accumulators retrieved from output queue
INFO:gensim.topic_coherence.text_analysis:accumulated word occurrence stats for 140566 virtual documents


11 Topics: 0.41451408010697643


INFO:gensim.topic_coherence.probability_estimation:using ParallelWordOccurrenceAccumulator(processes=3, batch_size=64) to estimate probabilities from sliding windows
INFO:gensim.topic_coherence.text_analysis:serializing accumulator to return to master...
INFO:gensim.topic_coherence.text_analysis:serializing accumulator to return to master...
INFO:gensim.topic_coherence.text_analysis:serializing accumulator to return to master...
INFO:gensim.topic_coherence.text_analysis:accumulator serialized
INFO:gensim.topic_coherence.text_analysis:accumulator serialized
INFO:gensim.topic_coherence.text_analysis:accumulator serialized
INFO:gensim.topic_coherence.text_analysis:3 accumulators retrieved from output queue
INFO:gensim.topic_coherence.text_analysis:accumulated word occurrence stats for 142693 virtual documents


13 Topics: 0.437763223430082


INFO:gensim.topic_coherence.probability_estimation:using ParallelWordOccurrenceAccumulator(processes=3, batch_size=64) to estimate probabilities from sliding windows
INFO:gensim.topic_coherence.text_analysis:serializing accumulator to return to master...
INFO:gensim.topic_coherence.text_analysis:serializing accumulator to return to master...
INFO:gensim.topic_coherence.text_analysis:accumulator serialized
INFO:gensim.topic_coherence.text_analysis:accumulator serialized
INFO:gensim.topic_coherence.text_analysis:serializing accumulator to return to master...
INFO:gensim.topic_coherence.text_analysis:accumulator serialized
INFO:gensim.topic_coherence.text_analysis:3 accumulators retrieved from output queue
INFO:gensim.topic_coherence.text_analysis:accumulated word occurrence stats for 149098 virtual documents


...

28 Topics: 0.46014799013580426


INFO:gensim.topic_coherence.probability_estimation:using ParallelWordOccurrenceAccumulator(processes=3, batch_size=64) to estimate probabilities from sliding windows
INFO:gensim.topic_coherence.text_analysis:serializing accumulator to return to master...
INFO:gensim.topic_coherence.text_analysis:serializing accumulator to return to master...
INFO:gensim.topic_coherence.text_analysis:accumulator serialized
INFO:gensim.topic_coherence.text_analysis:serializing accumulator to return to master...
INFO:gensim.topic_coherence.text_analysis:accumulator serialized
INFO:gensim.topic_coherence.text_analysis:accumulator serialized
INFO:gensim.topic_coherence.text_analysis:3 accumulators retrieved from output queue
INFO:gensim.topic_coherence.text_analysis:accumulated word occurrence stats for 149466 virtual documents


29 Topics: 0.4524502069223799


INFO:gensim.topic_coherence.probability_estimation:using ParallelWordOccurrenceAccumulator(processes=3, batch_size=64) to estimate probabilities from sliding windows
INFO:gensim.topic_coherence.text_analysis:serializing accumulator to return to master...
INFO:gensim.topic_coherence.text_analysis:accumulator serialized
INFO:gensim.topic_coherence.text_analysis:serializing accumulator to return to master...
INFO:gensim.topic_coherence.text_analysis:accumulator serialized
INFO:gensim.topic_coherence.text_analysis:serializing accumulator to return to master...
INFO:gensim.topic_coherence.text_analysis:accumulator serialized
INFO:gensim.topic_coherence.text_analysis:3 accumulators retrieved from output queue
INFO:gensim.topic_coherence.text_analysis:accumulated word occurrence stats for 149111 virtual documents


31 Topics: 0.45789325797326286


## Get Representative Post for each topic

In [156]:
import re
model_files = [f for f in glob("output/AskWomen_ldafinal*/*") if re.search(".*/\d+$", f)]

model_list = []
for f in model_files:
    mfile = open(f+"/model.pkl", "rb")
    model_list.append(pickle.load(mfile))
print(len(model_list))

17


In [184]:
observations = load_data_from_psql(["AskWomen"], table_name="preprocessed_posts")
print(str(observations.head()))
        
# Transform data
tokenized_data = transform(observations, ngrams=2, threshold=50)
id2word = corpora.Dictionary(tokenized_data)

texts = tokenized_data
corpus = [id2word.doc2bow(text) for text in texts]

           author       body subreddit
0       [deleted]  [deleted]  AskWomen
1       [deleted]  [deleted]  AskWomen
2       [deleted]  [deleted]  AskWomen
3       [deleted]  [deleted]  AskWomen
4  ffreudiannipss      No/no  AskWomen
Blacklists: data/filtering/author/reddit_bots.txt data/filtering/author/suspicious_authors.txt
Removing bots and suspicious authors
Preprocessing


INFO:gensim.models.phrases:collecting all words and their counts
INFO:gensim.models.phrases:PROGRESS: at sentence #0, processed 0 words and 0 word types
INFO:gensim.models.phrases:PROGRESS: at sentence #10000, processed 202077 words and 154846 word types
INFO:gensim.models.phrases:PROGRESS: at sentence #20000, processed 409477 words and 278687 word types
INFO:gensim.models.phrases:PROGRESS: at sentence #30000, processed 612497 words and 391448 word types
INFO:gensim.models.phrases:PROGRESS: at sentence #40000, processed 808830 words and 493732 word types
INFO:gensim.models.phrases:PROGRESS: at sentence #50000, processed 1005207 words and 589845 word types
INFO:gensim.models.phrases:PROGRESS: at sentence #60000, processed 1206103 words and 681011 word types
INFO:gensim.models.phrases:PROGRESS: at sentence #70000, processed 1414355 words and 773798 word types
INFO:gensim.models.phrases:PROGRESS: at sentence #80000, processed 1622576 words and 861280 word types
INFO:gensim.models.phrases:

In [185]:
model = model_list[0]
# have model, corpus, dictionary
# texts = ?? tokenized??

texts = [t for t in texts if len(t) > 0]
corpus = [c for c in corpus if len(c) > 0]

print(texts[:5])
print(corpus[:5])

[['til', 'dentists', 'work', 'government'], ['taylor_swift'], ['lose', 'shit', 'gumps', 'lol'], ['try', 'reply', 'someone'], ['man', 'bun']]
[[(0, 1), (1, 1), (2, 1), (3, 1)], [(4, 1)], [(5, 1), (6, 1), (7, 1), (8, 1)], [(9, 1), (10, 1), (11, 1)], [(12, 1), (13, 1)]]


In [194]:
for i, row in enumerate(model[corpus][:1]):
    print(row)

([(0, 0.15567528), (1, 0.03548565), (2, 0.22113779), (3, 0.09014028), (4, 0.101088025), (5, 0.03018133), (6, 0.035760038), (7, 0.036153577), (8, 0.034904383), (10, 0.16749379), (11, 0.08442)], [(0, [3]), (1, [4]), (2, [11]), (3, [2])], [(0, [(3, 0.99993855)]), (1, [(4, 0.99999994)]), (2, [(11, 1.0)]), (3, [(2, 1.0)])])


In [191]:
def format_topics_sentences(ldamodel, corpus, texts):
    sent_topics_df = pd.DataFrame()
    
    # Get main topic in each document
    for i, row in enumerate(ldamodel[corpus]):
        row = [i for i in row if len(i) > 0]
        print(row)
        row = sorted(row, key=lambda x: (x[1]), reverse=True)
        # Get Dominant topic, ratio, and keywords for each document
        for j, (topic_num, prop_topic) in enumerate(row):
            if j == 0: # dominant topic
                wp = ldamodel.show_topic(topic_num)
                topic_keywords = ", ".join([word for word, prop in wp])
                sent_topics_df.append(
                    pd.Series([int(topic_num),round(prop_topic,4),topic_keywords]),ignore_index=True, inplace=True)
            else:
                break
    sent_topics_df.columns = ['Dominant_Topic', 'Percent_Contrib', 'Topic_Keywords']
    
    # Add original text to the end
    contents = pd.Series(texts)
    sent_topics_df = pd.concat([sent_topics_df, contents], axis=1)
    return sent_topics_df

df_topic_sents_keywords = format_topics_sentences(ldamodel=model, corpus=corpus, texts=texts)
df_topic_sents_keywords.head()

[[(0, 0.15567528), (1, 0.03548565), (2, 0.22113779), (3, 0.09014028), (4, 0.101088025), (5, 0.03018133), (6, 0.035760038), (7, 0.036153577), (8, 0.034904383), (10, 0.16749379), (11, 0.084419996)], [(0, [3]), (1, [4]), (2, [11]), (3, [2])], [(0, [(3, 0.99993855)]), (1, [(4, 0.99999994)]), (2, [(11, 1.0)]), (3, [(2, 1.0)])]]


TypeError: '<' not supported between instances of 'int' and 'tuple'

TypeError: '<' not supported between instances of 'int' and 'tuple'